# "Letalidade e Mortalidade dos casos de SRAG-COVID nos municípios do Brasil"
> "Dados dos casos de hospitalizações por SRAG do opendatasus"

- toc: true
- branch: master
- badges: true
- comments: false
- numbersections: true
- categories: [srag, letalidade]
- image: images/some_folder/your_image.png
- hide: false
- search_exclude: true
- metadata_key1: metadata_value1
- metadata_key2: metadata_value2

## Informações sobre os dados utilizados

### Localização
- Páginas com informações completas sobre os conjuntos de dados: [2019](https://opendatasus.saude.gov.br/dataset/bd-srag-2019), [2020](https://opendatasus.saude.gov.br/dataset/bd-srag-2020), [2021](https://opendatasus.saude.gov.br/dataset/bd-srag-2021)

### Origem e contexto

Desde 2009, com a pandemia de Influenza A(H1N1)pdm09, a Secretaria de Vigilância em Saúde (SVS), vinculada ao Ministério da Saúde, desenvolve a vigilância da Síndrome Respiratória Aguda Grave (SRAG) no Brasil. Em 2020 a vigilância da COVID-19 foi incorporada na rede de vigilância da Influenza e outros vírus respiratórios.

Atualmente, o sistema oficial para o registro dos casos e óbitos de SRAG no Brasil é o Sistema de Informação da Vigilância Epidemiológica da Gripe (SIVEP-Gripe).

Todos os bancos de dados epidemiológicos de SRAG, desde 2009 até os dias atuais (2021), são disponibilizados no portal https://opendatasus.saude.gov.br. 

### Informações adicionais

- No Guia de Vigilância Epidemiológica Emergência de Saúde Pública de Importância Nacional pela Doença pelo Coronavírus 2019 estão disponíveis informações sobre definições de casos, critérios de confirmação e encerramento dos casos, dentre outros. [link](https://portalarquivos.saude.gov.br/images/af_gvs_coronavirus_6ago20_ajustes-finais-2.pdf)

- Os dados da vigilância de SRAG no Brasil disponibilizados estão sujeitos a alterações decorrentes da investigação pelas equipes de vigilância epidemiológica que desenvolvem o serviço nas três esferas de gestão.

- Os dados são disponibilizados semanalmente, às quartas-feiras, podendo, excepcionalmente, a atualização ocorrer em outro dia.

- Dicionários de dados: [2019](https://opendatasus.saude.gov.br/dataset/e99cfd21-3d8c-4ff9-bd9c-04b8b2518739/resource/457727e2-0401-4d5e-af7b-2f3bb2a7c652/download/dicionario_de_dados_srag_hospitalizado_atual-sivepgripe-2019.pdf), [2020](https://opendatasus.saude.gov.br/dataset/ae90fa8f-3e94-467e-a33f-94adbb66edf8/resource/8f571374-c555-4ec0-8e44-00b1e8b11c25/download/dicionario-de-dados-srag-hospitalizado-27.07.2020-final.pdf), [2021](https://opendatasus.saude.gov.br/dataset/9f76e80f-a2f1-4662-9e37-71084eae23e3/resource/b3321e55-24e9-49ab-8651-29cf5c8f3179/download/dicionario-de-dados-srag-hospitalizado-27.07.2020-final.pdf)

In [1]:
#hide
# %run update_srag_database.py

In [51]:
#hide

import sqlite3 as sql
import pandas as pd
import numpy as np
from srag_functions import *

db_name = 'srag'
db_path = f'data/opendatasus/{db_name}.db'
conn = sql.connect(db_path)
df_srag = pd.read_sql(f'SELECT * FROM {db_name} WHERE ano >= 2020', conn)

In [3]:
#hide

assert df_srag.shape[1]==32

### Dimensões dos dados: número de casos e características avaliadas

In [4]:
#hide

print('> Dimensões:\n')
print(f'\t{df_srag.shape[0]} linhas\n\t{df_srag.shape[1]} colunas')
print('\n> Colunas:')
for col,col_type in df_srag.dtypes.sort_index().items():
    print('\t{:<15}\t{:<}'.format(col,str(col_type)))
    
    
max_semana_visualizacao = df_srag.SEM_PRI_ABS.max() - 4

> Dimensões:

	2788012 linhas
	32 colunas

> Colunas:
	CLASSI_FIN     	object
	CLASSI_OUT     	object
	CO_MUN_NOT     	object
	CO_MUN_RES     	object
	CO_MU_INTE     	object
	CS_ESCOL_N     	object
	CS_RACA        	object
	CS_SEXO        	object
	DT_ENTUTI      	object
	DT_EVOLUCA     	object
	DT_NASC        	object
	DT_SIN_PRI     	object
	EVOLUCAO       	object
	FATOR_RISC     	object
	MUN_INTE       	object
	MUN_NOT        	object
	MUN_RES        	object
	NU_IDADE_N     	int64
	REGIAO_INTE    	object
	REGIAO_NOT     	object
	REGIAO_RES     	object
	SATURACAO      	object
	SEM_PRI        	int64
	SEM_PRI_ABS    	int64
	SUPORT_VEN     	object
	UF_INTE        	object
	UF_NOT         	object
	UF_RES         	object
	UTI            	object
	ano            	int64
	faixa_etaria   	object
	idade_anos     	float64


### Número de casos avaliados
[Topo](/covid/srag/letalidade/2021/04/13/letalidade-srag.html#)
> construção do df_pop_mun

In [37]:
#hide_input
#collapse_output

print(f'{df_srag.shape[0]} casos de SRAG.')

df = df_srag.loc[df_srag.CLASSI_FIN == 'COVID-19'].copy()

df.loc[df.UF_RES == '53_Distrito Federal','CO_MUN_RES'] = '530010'

print(f'{df.shape[0]} casos de SRAG-COVID.')
df = df.loc[df.EVOLUCAO.isin(['obito', 'cura', 'obito_outras_causas'])]
print(f'{df.shape[0]} casos de SRAG-COVID concluídos.')
df = df.groupby(['CO_MUN_RES','EVOLUCAO'],as_index=False).size()
df = df.pivot(index = 'CO_MUN_RES',columns='EVOLUCAO',values='size')
# df = df[['cura','obito', 'obito_outras_causas']].fillna(0)
df_mun_dict = df.fillna(0).to_dict()
df = df.reset_index()

file_pop_mun = 'data/IBGE/Tabela_6579_populacao_residente_estimada.csv'


df_pop_mun = pd.read_csv(file_pop_mun,header=3).dropna().rename(columns={'2020':'População (2020)'})

# df_pop_mun = pd.read_(file_pop_mun,header=2)
# cols = df_pop_mun.iloc[0,:-1].to_list() + df_pop_mun.columns[0].split()[-1:]
# df_pop_mun.columns=cols
# df_pop_mun = df_pop_mun.iloc[1:-1]
df_pop_mun['cod6_mun'] = df_pop_mun['Cód.'].str[:6]
df_pop_mun['cura'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['cura'].get(x,0))
df_pop_mun['obito'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['obito'].get(x,0))
df_pop_mun['obito_outras_causas'] = df_pop_mun['cod6_mun'].apply(lambda x: df_mun_dict['obito_outras_causas'].get(x,0))
df_pop_mun['casos_concluidos'] = df_pop_mun['cura'] + df_pop_mun['obito'] + df_pop_mun['obito_outras_causas']
df_pop_mun['letalidade'] = df_pop_mun['obito'] / df_pop_mun['casos_concluidos']
# df_pop_mun['letalidade'] = df_pop_mun['obito'].apply(lambda x: 0 if x==0 else )
df_pop_mun['mortalidade'] = df_pop_mun['obito'] / df_pop_mun['População (2020)']
df_pop_mun = df_pop_mun.fillna(0)
casos_mun_res = df_pop_mun['casos_concluidos'].sum()
print(f'{int(casos_mun_res)} casos de SRAG-COVID concluídos com dados de município de residência.')
df_pop_mun


2788012 casos de SRAG.
1843286 casos de SRAG-COVID.
1687395 casos de SRAG-COVID concluídos.
1687169 casos de SRAG-COVID concluídos com dados de município de residência.


Cód.                   Município  População (2020) cod6_mun     cura  \
0     1100015  Alta Floresta D'Oeste (RO)           22728.0   110001     49.0   
1     1100023              Ariquemes (RO)          109523.0   110002    292.0   
2     1100031                 Cabixi (RO)            5188.0   110003      2.0   
3     1100049                 Cacoal (RO)           85893.0   110004    201.0   
4     1100056             Cerejeiras (RO)           16204.0   110005     65.0   
...       ...                         ...               ...      ...      ...   
5565  5222005             Vianópolis (GO)           13977.0   522200     63.0   
5566  5222054         Vicentinópolis (GO)            8873.0   522205     72.0   
5567  5222203               Vila Boa (GO)            6312.0   522220      8.0   
5568  5222302          Vila Propício (GO)            5882.0   522230      4.0   
5569  5300108               Brasília (DF)         3055149.0   530010  27473.0   

        obito  obito_outras_causas  casos_concluidos  letalidade  mortalidade  
0        58.0                  0.0             107.0    0.542056     0.002552  
1       490.0                  2.0             784.0    0.625000     0.004474  
2         4.0                  0.0               6.0    0.666667     0.000771  
3       208.0                  2.0             411.0    0.506083     0.002422  
4        46.0                  0.0             111.0    0.414414     0.002839  
...       ...                  ...               ...         ...          ...  
5565     36.0                  0.0              99.0    0.363636     0.002576  
5566     24.0                  0.0              96.0    0.250000     0.002705  
5567      4.0                  0.0              12.0    0.333333     0.000634  
5568      8.0                  0.0              12.0    0.666667     0.001360  
5569  10165.0                348.0           37986.0    0.267599     0.003327  

[5570 rows x 10 columns]

### Letalidade por Município
[Topo](/covid/srag/letalidade/2021/04/13/letalidade-srag.html#)

> Municípios com população acima de 4.000 habitantes (2020)

In [40]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 4000]
# df = df.sort_values(by='letalidade',ascending=False).reset_index(drop=True)
df = df.reset_index()

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('letalidade:Q', bin=alt.Bin(maxbins=20)),
    alt.Y('count()', stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


alt.Chart(...)

> Municípios com população acima de 10.000 habitantes (2020)

In [44]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 10000]
# df = df.sort_values(by='letalidade',ascending=False).reset_index(drop=True)
df = df.reset_index()

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('letalidade:Q', bin=alt.Bin(maxbins=20)),
    alt.Y('count()', stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


alt.Chart(...)

### Mortalidade por Município
[Topo](/covid/srag/letalidade/2021/04/13/letalidade-srag.html#)

> Municípios com população acima de 10.000 habitantes (2020)

In [49]:
#hide_input
#collapse_output

# df = df_pop_mun.sort_values(by='População (2020)',ascending=False).head(5000)
df = df_pop_mun.loc[df_pop_mun['População (2020)']>= 10000]
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
df = df.reset_index()
df['mortalidade'] = df['mortalidade']*100000

df=df.rename({'mortalidade':'mortalidade por 100.000 hab'})

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('mortalidade:Q', bin=alt.Bin(maxbins=20)),
    alt.Y('count()', stack=None),
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart


alt.Chart(...)

### Letalidade e mortalidade vs percentual da população rural
[Topo](/covid/srag/letalidade/2021/04/13/letalidade-srag.html#)

> Municípios com população acima de 4.000 habitantes (2020)

In [77]:
#hide

# adição da coluna com percentual de população rural (censo 2010)

file_name = 'data/IBGE/tabela761_urbano_rural_censo_2010.csv'

df = pd.read_csv(file_name,header=4)
df = df.dropna()
df.Rural = df.Rural.replace('-','0').astype(float)
# cols = df_pop_mun.iloc[0,:-1].to_list() + df_pop_mun.columns[0].split()[-1:]
# df_pop_mun.columns=cols
# df_pop_mun = df_pop_mun.iloc[1:-1]
df['cod6_mun'] = df['Cód.'].str[:6]
df['percent_rural'] = df['Rural'] / df['Total']
df = df.set_index('cod6_mun')['percent_rural']
dict_perc_rural = df.to_dict()
dict_perc_rural

df_pop_mun_2 = df_pop_mun.copy()
df_pop_mun_2['percent_rural'] = df_pop_mun_2['cod6_mun'].apply(lambda x: dict_perc_rural.get(x,np.nan)).dropna()
# df_pop_mun = df_pop_mun.dropna()
# df_pop_mun.loc[df_pop_mun.percent_rural.isna()]
df_pop_mun_2

# df = df_pop_mun.dropna().iloc[:nrows,1:]
delta = 10
df_pop_mun_2['cat_rur'] = df_pop_mun_2['percent_rural'].apply(lambda x : f'{int(x *100 / delta)*delta:02d}_{((int(x *100 / delta) + 1)*delta)}' )
df_pop_mun_2


Cód.                   Município  População (2020) cod6_mun     cura  \
0     1100015  Alta Floresta D'Oeste (RO)           22728.0   110001     49.0   
1     1100023              Ariquemes (RO)          109523.0   110002    292.0   
2     1100031                 Cabixi (RO)            5188.0   110003      2.0   
3     1100049                 Cacoal (RO)           85893.0   110004    201.0   
4     1100056             Cerejeiras (RO)           16204.0   110005     65.0   
...       ...                         ...               ...      ...      ...   
5565  5222005             Vianópolis (GO)           13977.0   522200     63.0   
5566  5222054         Vicentinópolis (GO)            8873.0   522205     72.0   
5567  5222203               Vila Boa (GO)            6312.0   522220      8.0   
5568  5222302          Vila Propício (GO)            5882.0   522230      4.0   
5569  5300108               Brasília (DF)         3055149.0   530010  27473.0   

        obito  obito_outras_causas  casos_concluidos  letalidade  mortalidade  \
0        58.0                  0.0             107.0    0.542056     0.002552   
1       490.0                  2.0             784.0    0.625000     0.004474   
2         4.0                  0.0               6.0    0.666667     0.000771   
3       208.0                  2.0             411.0    0.506083     0.002422   
4        46.0                  0.0             111.0    0.414414     0.002839   
...       ...                  ...               ...         ...          ...   
5565     36.0                  0.0              99.0    0.363636     0.002576   
5566     24.0                  0.0              96.0    0.250000     0.002705   
5567      4.0                  0.0              12.0    0.333333     0.000634   
5568      8.0                  0.0              12.0    0.666667     0.001360   
5569  10165.0                348.0           37986.0    0.267599     0.003327   

      percent_rural cat_rur  
0          0.427271   40_50  
1          0.153044   10_20  
2          0.573420   50_60  
3          0.211940   20_30  
4          0.153268   10_20  
...             ...     ...  
5565       0.269206   20_30  
5566       0.142450   10_20  
5567       0.260401   20_30  
5568       0.707677   70_80  
5569       0.034220   00_10  

[5565 rows x 12 columns]

In [72]:
#hide_input
#collapse_output

df = df_pop_mun_2.loc[df_pop_mun_2['População (2020)']>= 4000].copy()
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
# df = df.reset_index()
df['mortalidade'] = df['mortalidade']*100000

# df=df.rename(columns={'mortalidade':'mortalidade por 100.000 hab'})

chart = alt.Chart(df).mark_circle(size=20)
chart = chart.encode(
    alt.X('percent_rural:Q'),
    alt.Y('mortalidade:Q'),
    color='letalidade',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)

In [75]:
#hide_input
#collapse_output

df = df_pop_mun_2.loc[df_pop_mun_2['População (2020)']>= 4000].copy()
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
# df = df.reset_index()
df['mortalidade'] = df['mortalidade']*100000

# df=df.rename(columns={'mortalidade':'mortalidade por 100.000 hab'})

chart = alt.Chart(df).mark_bar()
chart = chart.encode(
    alt.X('mortalidade:Q', bin=alt.Bin(maxbins=20)),
    alt.Y('count()', stack=None),

    # color='letalidade',
    # tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)

In [69]:
#hide

df = df_pop_mun_2.loc[df_pop_mun_2['População (2020)']>= 4000].copy()
# df = df.sort_values(by='mortalidade',ascending=False).reset_index(drop=True)
# df = df.reset_index()
df['mortalidade'] = df['mortalidade']*100000

y_col='mortalidade por 100.000 hab'
y_col = 'mortalidade'
# df=df.rename(columns={'mortalidade':y_col})

chart = alt.Chart(df).mark_circle(size=20)
chart = chart.encode(
    alt.X('letalidade:Q'),
    alt.Y(f'{y_col}'),
    # color='percent_rural',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)

cat_rur  População (2020)      cura     obito  obito_outras_causas  \
0   00_10       129816963.0  825249.0  428030.0               2754.0   
1   10_20        22074936.0  109611.0   55801.0                372.0   
2   20_30        15992696.0   57615.0   34473.0                244.0   
3   30_40        12364067.0   38953.0   22107.0                218.0   
4   40_50        10900421.0   26417.0   16310.0                180.0   
5   50_60         9739872.0   21363.0   13649.0                149.0   
6   60_70         6609457.0   13270.0    8176.0                 92.0   
7   70_80         3239412.0    5727.0    3396.0                 42.0   
8   80_90          871331.0    1503.0     835.0                  6.0   
9  90_100           98558.0     186.0     101.0                  1.0   

   casos_concluidos  letalidade  mortalidade  percent_rural  
0         1256033.0    0.340779   329.718082      37.673592  
1          165784.0    0.336589   252.779895     124.700911  
2           92332.0    0.373359   215.554651     196.930072  
3           61278.0    0.360766   178.800390     277.608014  
4           42907.0    0.380124   149.627248     343.189446  
5           35161.0    0.388186   140.135312     370.638893  
6           21538.0    0.379608   123.701539     344.410448  
7            9165.0    0.370540   104.833840     228.529529  
8            2344.0    0.356229    95.830402      81.112294  
9             288.0    0.350694   102.477729       8.267541

In [81]:
#hide
#collapse_output

df = df_pop_mun_2.groupby('cat_rur').sum().reset_index()
df['letalidade'] = df['obito'] / df['casos_concluidos']
df['mortalidade'] = 100000* (df['obito'] / df['População (2020)'])

chart = alt.Chart(df).mark_bar(size=60) 

x_col = 'cat_rur'
x_col_ed = x_col
# x_col_ed=alt.X(f'{x_col}:N', sort='y')
   
chart = chart.encode(
    x=x_col_ed,
    y='mortalidade',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )
chart

alt.Chart(...)

In [82]:
#hide
#collapse_output

chart = alt.Chart(df).mark_bar() 

x_col = 'cat_rur'
x_col_ed = x_col
# x_col_ed=alt.X(f'{x_col}:N', sort='y')
   
chart = chart.encode(
    x=x_col_ed,
    y='letalidade',
    tooltip=list(df.columns)
    ).properties(
        width=600,
        height=400
    )
chart

alt.Chart(...)

In [86]:
#hide


def cat_pop(pop:float):
    if pop <= 5000:
        cat = '0. até 5 mil'
    elif pop <= 10000:
        cat = '1. 5 a 10 mil'
    elif pop <=20000:
        cat = '2. 10 a 20 mil'
    elif pop <= 50000:
        cat = '3. 20 a 50 mil'
    elif pop <= 200000:
        cat = '4. 50 a 200 mil'
    elif pop <= 500000:
        cat = '5. 200 a 500 mil'
    elif pop <= 1000000:
        cat = '6. 500 mil a 1MM'
    else: #pop >= 1e6:
        cat = '7. > 1MM'
    
    return cat

# nrows = 6000
df_pop = df_pop_mun_2.dropna().iloc[:,1:]
# delta = 10
df_pop['cat_pop'] = df_pop['População (2020)'].apply(lambda x : cat_pop(x) )
# df_pop.groupby('cat_pop').size()
df_pop = df_pop.groupby('cat_pop').sum().reset_index()
df_pop


cat_pop  População (2020)      cura     obito  \
0      0. até 5 mil         4183314.0   16885.0    8555.0   
1     1. 5 a 10 mil         8541879.0   29126.0   16009.0   
2    2. 10 a 20 mil        19024578.0   61506.0   34249.0   
3    3. 20 a 50 mil        33828245.0  126176.0   68642.0   
4   4. 50 a 200 mil        47006431.0  233132.0  121753.0   
5  5. 200 a 500 mil        31601488.0  178521.0   97145.0   
6  6. 500 mil a 1MM        21121066.0  129169.0   68480.0   
7          7. > 1MM        46400712.0  325379.0  168045.0   

   obito_outras_causas  casos_concluidos  letalidade  mortalidade  \
0                 53.0           25493.0  476.495246     2.609251   
1                112.0           45247.0  498.168379     2.245909   
2                269.0           96024.0  555.161616     2.392162   
3                576.0          195394.0  459.162746     2.226822   
4                903.0          355788.0  205.417234     1.314800   
5                435.0          276101.0   40.094862     0.320968   
6                616.0          198265.0   12.141638     0.102821   
7               1094.0          494518.0    6.185159     0.059778   

   percent_rural  
0     553.493430  
1     487.228455  
2     526.801186  
3     351.188365  
4      88.953531  
5       4.578385  
6       0.682417  
7       0.134971

In [88]:
#hide
#collapse_output

df = df_pop.groupby('cat_pop').sum().reset_index()
df['letalidade'] = df['obito'] / df['casos_concluidos']
df['mortalidade'] = 100000* (df['obito'] / df['População (2020)'])

chart = alt.Chart(df).mark_bar() 

x_col = 'cat_pop'
# sort_axis = 'x'
x_col_ed = x_col
# x_col_ed=alt.X(f'{x_col}:N', sort='y')
   
chart = chart.encode(
    x=x_col_ed,
    color='mortalidade',
    y='letalidade',
    # y='mortalidade',
    # color='letalidade',
    tooltip=list(df_pop.columns)
    ).properties(
        width=600,
        height=400
    )#.interactive()
chart

alt.Chart(...)